In [1]:
def basis_holomorphic_differentials_degree(f, m, p):
    r = f.degree()
    delta = GCD(r, m)
    Rx.<x> = PolynomialRing(GF(p))
    Rxy.<x, y> = PolynomialRing(GF(p), 2)
    Fxy = FractionField(Rxy)
    #########basis of holomorphic differentials and de Rham
                
    basis_holo = []
    degrees0 = {}
    k = 0
        
    for j in range(1, m):
        for i in range(1, r):
            if (r*j - m*i >= delta):
                basis_holo += [Fxy(x^(i-1)/y^j)]
                degrees0[k] = (i-1, j)
                k = k+1
                    
    return(basis_holo, degrees0)

def holomorphic_differentials_basis(f, m, p):
        basis_holo, degrees0 = basis_holomorphic_differentials_degree(f, m, p)
        return basis_holo
        
def degrees_holomorphic_differentials(f, m, p):
    basis_holo, degrees0 = basis_holomorphic_differentials_degree(f, m, p)
    return degrees0
    
def basis_de_rham_degrees(f, m, p):
    r = f.degree()
    delta = GCD(r, m)
    Rx.<x> = PolynomialRing(GF(p))
    Rxy.<x, y> = PolynomialRing(GF(p), 2)
    Fxy = FractionField(Rxy)
    basis_holo = holomorphic_differentials_basis(f, m, p)
    basis = []
    for k in range(0, len(basis_holo)):
        basis += [(basis_holo[k], Rx(0))]

    ## non-holomorphic elts of H^1_dR
    t = len(basis)
    degrees0 = {}
    degrees1 = {}
    for j in range(1, m):
        for i in range(1, r):
            if (r*(m-j) - m*i >= delta): 
                s = Rx(m-j)*Rx(x)*Rx(f.derivative()) - Rx(m)*Rx(i)*f
                psi = Rx(cut(s, i))
                basis += [(Fxy(psi/y^j), Fxy(m*y^(m-j)/x^i))]
                degrees0[t] = (psi.degree(), j)
                degrees1[t] = (-i, m-j)
                t += 1
    return basis, degrees0, degrees1

def de_rham_basis(f, m, p):
    basis, degrees0, degrees1 = basis_de_rham_degrees(f, m, p)
    return basis

def degrees_de_rham0(f, m, p):
    basis, degrees0, degrees1 = basis_de_rham_degrees(f, m, p)
    return degrees0

def degrees_de_rham1(f, m, p):
    basis, degrees0, degrees1 = basis_de_rham_degrees(f, m, p)
    return degrees1    


class superelliptic:
    
    def __init__(self, f, m, p):
        Rx.<x> = PolynomialRing(GF(p))
        Rxy.<x, y> = PolynomialRing(GF(p), 2)
        Fxy = FractionField(Rxy)
        self.polynomial = Rx(f)
        self.exponent = m
        self.characteristic = p
        
        r = Rx(f).degree()
        delta = GCD(r, m)
        self.degree_holo = degrees_holomorphic_differentials(f, m, p)
        self.degree_de_rham0 = degrees_de_rham0(f, m, p)
        self.degree_de_rham1 = degrees_de_rham1(f, m, p)
        
        holo_basis = holomorphic_differentials_basis(f, m, p)
        holo_basis_converted = []
        for a in holo_basis:
            holo_basis_converted += [superelliptic_form(self, a)]
        
        self.basis_holomorphic_differentials = holo_basis_converted
        

        dr_basis = de_rham_basis(f, m, p)
        dr_basis_converted = []
        for (a, b) in dr_basis:
            dr_basis_converted += [superelliptic_cech(self, superelliptic_form(self, a), superelliptic_function(self, b))]
        
        self.basis_de_rham = dr_basis_converted
        
    def __repr__(self):
        f = self.polynomial
        m = self.exponent
        p = self.characteristic
        return 'Superelliptic curve with the equation y^' + str(m) + ' = ' + str(f)+' over finite field with ' + str(p) + ' elements.'
    
    def is_smooth(self):
        f = self.polynomial
        if f.discriminant() == 0:
            return 0
        return 1
    
    def genus(self):
        r = self.polynomial.degree()
        m = self.exponent
        delta = GCD(r, m)
        return 1/2*((r-1)*(m-1) - delta + 1)
    
    def verschiebung_matrix(self):
        basis = self.basis_de_rham
        g = self.genus()
        p = self.characteristic
        M = matrix(GF(p), 2*g, 2*g)
        for i in range(0, len(basis)):
            w = basis[i]
            v = w.verschiebung().coordinates()
            M[i, :] = v
        return M
    
    def frobenius_matrix(self):
        basis = self.basis_de_rham
        g = self.genus()
        p = self.characteristic
        M = matrix(GF(p), 2*g, 2*g)
        
        for i in range(0, len(basis)):
            w = basis[i]
            v = w.frobenius().coordinates()
            M[i, :] = v
        return M

    def cartier_matrix(self):
        basis = self.basis_holomorphic_differentials
        g = self.genus()
        p = self.characteristic
        M = matrix(GF(p), g, g)
        for i in range(0, len(basis)):
            w = basis[i]
            v = w.cartier().coordinates()
            M[i, :] = v
        return M     
    
    def p_rank(self):
        return self.cartier_matrix().rank()
    
    def final_type(self, test = 0):
        F = self.frobenius_matrix()
        V = self.verschiebung_matrix()
        p = self.characteristic
        return flag(F, V, p, test)
    
def reduction(C, g):
    p = C.characteristic
    Rxy.<x, y> = PolynomialRing(GF(p), 2)
    Fxy = FractionField(Rxy)
    f = C.polynomial
    r = f.degree()
    m = C.exponent
    g = Fxy(g)
    g1 = g.numerator()
    g2 = g.denominator()
    
    Rx.<x> = PolynomialRing(GF(p))
    Fx = FractionField(Rx)
    FxRy.<y> = PolynomialRing(Fx)    
    (A, B, C) = xgcd(FxRy(g2), FxRy(y^m - f))
    g = FxRy(g1*B/A)
    
    while(g.degree(Rxy(y)) >= m):
        d = g.degree(Rxy(y))
        G = coff(g, d)
        i = floor(d/m)
        g = g - G*y^d + f^i * y^(d%m) *G
    
    return(FxRy(g))

def reduction_form(C, g):
    p = C.characteristic
    Rxy.<x, y> = PolynomialRing(GF(p), 2)
    Fxy = FractionField(Rxy)
    f = C.polynomial
    r = f.degree()
    m = C.exponent
    g = reduction(C, g)

    g1 = Rxy(0)
    Rx.<x> = PolynomialRing(GF(p))
    Fx = FractionField(Rx)
    FxRy.<y> = PolynomialRing(Fx)
    
    g = FxRy(g)
    for j in range(0, m):
        if j==0:
            G = coff(g, 0)
            g1 += FxRy(G)
        else:
            G = coff(g, j)
            g1 += Fxy(y^(j-m)*f*G)
    return(g1)
        
class superelliptic_function:
    def __init__(self, C, g):
        p = C.characteristic
        Rxy.<x, y> = PolynomialRing(GF(p), 2)
        Fxy = FractionField(Rxy)
        f = C.polynomial
        r = f.degree()
        m = C.exponent
        
        self.curve = C
        g = reduction(C, g)
        self.function = g
        
    def __repr__(self):
        return str(self.function)
    
    def jth_component(self, j):
        g = self.function
        C = self.curve
        p = C.characteristic
        Rx.<x> = PolynomialRing(GF(p))
        Fx.<x> = FractionField(Rx)
        FxRy.<y> = PolynomialRing(Fx)
        g = FxRy(g)
        return coff(g, j)
    
    def __add__(self, other):
        C = self.curve
        g1 = self.function
        g2 = other.function
        g = reduction(C, g1 + g2)
        return superelliptic_function(C, g)
    
    def __sub__(self, other):
        C = self.curve
        g1 = self.function
        g2 = other.function
        g = reduction(C, g1 - g2)
        return superelliptic_function(C, g)
    
    def __mul__(self, other):
        C = self.curve
        g1 = self.function
        g2 = other.function
        g = reduction(C, g1 * g2)
        return superelliptic_function(C, g)
    
    def __truediv__(self, other):
        C = self.curve
        g1 = self.function
        g2 = other.function
        g = reduction(C, g1 / g2)
        return superelliptic_function(C, g)
    
def diffn(self):
    C = self.curve
    f = C.polynomial
    m = C.exponent
    p = C.characteristic
    g = self.function
    Rxy.<x, y> = PolynomialRing(GF(p), 2)
    Fxy = FractionField(Rxy)
    g = Fxy(g)
    A = g.derivative(x)
    B = g.derivative(y)*f.derivative(x)/(m*y^(m-1))
    return superelliptic_form(C, A+B)
        
class superelliptic_form:
    def __init__(self, C, g):
        p = C.characteristic
        Rxy.<x, y> = PolynomialRing(GF(p), 2)
        Fxy = FractionField(Rxy)
        g = Fxy(reduction_form(C, g))
        self.form = g
        self.curve = C      
        
    def __add__(self, other):
        C = self.curve
        g1 = self.form
        g2 = other.form
        g = reduction(C, g1 + g2)
        return superelliptic_form(C, g)
    
    def __sub__(self, other):
        C = self.curve
        g1 = self.form
        g2 = other.form
        g = reduction(C, g1 - g2)
        return superelliptic_form(C, g)
    
    def __repr__(self):
        g = self.form
        if len(str(g)) == 1:
            return str(g) + ' dx'
        return '('+str(g) + ') dx'

    def __rmul__(self, constant):
        C = self.curve
        omega = self.form
        return superelliptic_form(C, constant*omega)        
    
    def cartier(self):
        C = self.curve
        m = C.exponent
        p = C.characteristic
        f = C.polynomial
        Rx.<x> = PolynomialRing(GF(p))
        Fx = FractionField(Rx)
        FxRy.<y> = PolynomialRing(Fx)
        Fxy = FractionField(FxRy)
        result = superelliptic_form(C, FxRy(0))
        mult_order = Integers(m)(p).multiplicative_order()
        M = Integer((p^(mult_order)-1)/m)
        
        for j in range(1, m):
            fct_j = self.jth_component(j)
            h = Rx(fct_j*f^(M*j))
            j1 = (p^(mult_order-1)*j)%m
            B = floor(p^(mult_order-1)*j/m)
            result += superelliptic_form(C, polynomial_part(p, h)/(f^B*y^(j1)))
        return result   
    
    def coordinates(self):
        C = self.curve
        p = C.characteristic
        m = C.exponent
        Rx.<x> = PolynomialRing(GF(p))
        Fx = FractionField(Rx)
        FxRy.<y> = PolynomialRing(Fx)
        g = C.genus()
        degrees_holo = C.degree_holo
        degrees_holo_inv = {b:a for a, b in degrees_holo.items()}
        basis = C.basis_holomorphic_differentials
        
        for j in range(1, m):
            omega_j = Fx(self.jth_component(j))
            if omega_j != Fx(0):
                d = degree_of_rational_fctn(omega_j, p)
                index = degrees_holo_inv[(d, j)]
                a = coeff_of_rational_fctn(omega_j, p)
                a1 = coeff_of_rational_fctn(basis[index].jth_component(j), p)
                elt = self - (a/a1)*basis[index]
                return elt.coordinates() + a/a1*vector([GF(p)(i == index) for i in range(0, g)])
            
        return vector(g*[0])
    
    def jth_component(self, j):
        g = self.form
        C = self.curve
        p = C.characteristic
        Rx.<x> = PolynomialRing(GF(p))
        Fx = FractionField(Rx)
        FxRy.<y> = PolynomialRing(Fx)
        Fxy = FractionField(FxRy)
        Ryinv.<y_inv> = PolynomialRing(Fx)
        g = Fxy(g)
        g = g(y = 1/y_inv)
        g = Ryinv(g)
        return coff(g, j)
    
    def is_regular_on_U0(self):
        C = self.curve
        p = C.characteristic
        m = C.exponent
        Rx.<x> = PolynomialRing(GF(p))
        for j in range(1, m):
            if self.jth_component(j) not in Rx:
                return 0
        return 1
    
    def is_regular_on_Uinfty(self):
        C = self.curve
        p = C.characteristic
        m = C.exponent
        f = C.polynomial
        r = f.degree()
        delta = GCD(m, r)
        M = m/delta
        R = r/delta
        
        for j in range(1, m):
            A = self.jth_component(j)
            d = degree_of_rational_fctn(A, p)
            if(-d*M + j*R -(M+1)<0):
                return 0
        return 1
    
    
class superelliptic_cech:
    def __init__(self, C, omega, fct):
        self.omega0 = omega
        self.omega8 = omega - diffn(fct)
        self.f = fct
        self.curve = C
        
    def __add__(self, other):
        C = self.curve
        return superelliptic_cech(C, self.omega0 + other.omega0, self.f + other.f)
    
    def __sub__(self, other):
        C = self.curve
        return superelliptic_cech(C, self.omega0 - other.omega0, self.f - other.f)

    def __rmul__(self, constant):
        C = self.curve
        w1 = self.omega0.form
        f1 = self.f.function
        w2 = superelliptic_form(C, constant*w1)
        f2 = superelliptic_function(C, constant*f1)
        return superelliptic_cech(C, w2, f2)    
    
    def __repr__(self):
        return "(" + str(self.omega0) + ", " + str(self.f) + ", " + str(self.omega8) + ")" 
    
    def verschiebung(self):
        C = self.curve
        omega = self.omega0
        p = C.characteristic
        Rx.<x> = PolynomialRing(GF(p))
        return superelliptic_cech(C, omega.cartier(), superelliptic_function(C, Rx(0)))
    
    def frobenius(self):
        C = self.curve
        fct = self.f.function
        p = C.characteristic
        Rx.<x> = PolynomialRing(GF(p))
        return superelliptic_cech(C, superelliptic_form(C, Rx(0)), superelliptic_function(C, fct^p))

    def coordinates(self):
        C = self.curve
        p = C.characteristic
        m = C.exponent
        Rx.<x> = PolynomialRing(GF(p))
        Fx = FractionField(Rx)
        FxRy.<y> = PolynomialRing(Fx)
        g = C.genus()
        degrees_holo = C.degree_holo
        degrees_holo_inv = {b:a for a, b in degrees_holo.items()}
        degrees0 = C.degree_de_rham0
        degrees0_inv = {b:a for a, b in degrees0.items()}
        degrees1 = C.degree_de_rham1
        degrees1_inv = {b:a for a, b in degrees1.items()}
        basis = C.basis_de_rham
        
        omega = self.omega0
        fct = self.f
        
        if fct.function == Rx(0) and omega.form != Rx(0):
            for j in range(1, m):
                omega_j = Fx(omega.jth_component(j))
                if omega_j != Fx(0):
                    d = degree_of_rational_fctn(omega_j, p)
                    index = degrees_holo_inv[(d, j)]
                    a = coeff_of_rational_fctn(omega_j, p)
                    a1 = coeff_of_rational_fctn(basis[index].omega0.jth_component(j), p)
                    elt = self - (a/a1)*basis[index]
                    return elt.coordinates() + a/a1*vector([GF(p)(i == index) for i in range(0, 2*g)])
                    
        for j in range(1, m):
            fct_j = Fx(fct.jth_component(j))
            if (fct_j != Rx(0)):
                d = degree_of_rational_fctn(fct_j, p)
            
                if (d, j) in degrees1.values():
                    index = degrees1_inv[(d, j)]
                    a = coeff_of_rational_fctn(fct_j, p)
                    elt = self - (a/m)*basis[index]
                    return elt.coordinates() + a/m*vector([GF(p)(i == index) for i in range(0, 2*g)])
                
                if d<0:
                    a = coeff_of_rational_fctn(fct_j, p)
                    h = superelliptic_function(C, FxRy(a*y^j*x^d))
                    elt = superelliptic_cech(C, self.omega0, self.f - h)
                    return elt.coordinates()
            
                if (fct_j != Rx(0)):
                    G = superelliptic_function(C, y^j*x^d)
                    a = coeff_of_rational_fctn(fct_j, p)
                    elt =self - a*superelliptic_cech(C, diffn(G), G)
                    return elt.coordinates()

        return vector(2*g*[0])
    
    def is_cocycle(self):
        w0 = self.omega0
        w8 = self.omega8
        fct = self.f
        if not w0.is_regular_on_U0() and not w8.is_regular_on_Uinfty():
            return('w0 & w8')
        if not w0.is_regular_on_U0():
            return('w0')
        if not w8.is_regular_on_Uinfty():
            return('w8')
        if w0.is_regular_on_U0() and w8.is_regular_on_Uinfty():
            return 1
        return 0
        
def degree_of_rational_fctn(f, p):
    Rx.<x> = PolynomialRing(GF(p))
    Fx = FractionField(Rx)
    f = Fx(f)
    f1 = f.numerator()
    f2 = f.denominator()
    d1 = f1.degree()
    d2 = f2.degree()
    return(d1 - d2)

def coeff_of_rational_fctn(f, p):
    Rx.<x> = PolynomialRing(GF(p))
    Fx = FractionField(Rx)
    f = Fx(f)
    if f == Rx(0):
        return 0
    f1 = f.numerator()
    f2 = f.denominator()
    d1 = f1.degree()
    d2 = f2.degree()
    a1 = f1.coefficients(sparse = false)[d1]
    a2 = f2.coefficients(sparse = false)[d2]
    return(a1/a2)

def coff(f, d):
    lista = f.coefficients(sparse = false)
    if len(lista) <= d:
        return 0
    return lista[d]

def cut(f, i):
    R = f.parent()
    coeff = f.coefficients(sparse = false)
    return sum(R(x^(j-i-1)) * coeff[j] for j in range(i+1, f.degree() + 1))

def polynomial_part(p, h):
    Rx.<x> = PolynomialRing(GF(p))
    h = Rx(h)
    result = Rx(0)
    for i in range(0, h.degree()+1):
        if (i%p) == p-1:
            power = Integer((i-(p-1))/p)
            result += Integer(h[i]) * x^(power)    
    return result

In [2]:
def preimage(U, V, M): #preimage of subspace U under M
    basis_preimage = M.right_kernel().basis()
    imageU = U.intersection(M.transpose().image())
    basis = imageU.basis()
    for v in basis:
        w = M.solve_right(v)
        basis_preimage = basis_preimage + [w]
    return V.subspace(basis_preimage)

def image(U, V, M):
    basis = U.basis()
    basis_image = []
    for v in basis:
        basis_image += [M*v]
    return V.subspace(basis_image)

def flag(F, V, p, test = 0):
    dim = F.dimensions()[0]
    space = VectorSpace(GF(p), dim)
    flag_subspaces = (dim+1)*[0]
    flag_used = (dim+1)*[0]
    final_type = (dim+1)*['?']
    
    flag_subspaces[dim] = space
    flag_used[dim] = 1
   
    
    while 1 in flag_used:
        index = flag_used.index(1)
        flag_used[index] = 0
        U = flag_subspaces[index]
        U_im = image(U, space, V)
        d_im = U_im.dimension()
        final_type[index] = d_im
        U_pre = preimage(U, space, F)
        d_pre = U_pre.dimension()
        
        if flag_subspaces[d_im] == 0:
            flag_subspaces[d_im] = U_im
            flag_used[d_im] = 1
        
        if flag_subspaces[d_pre] == 0:
            flag_subspaces[d_pre] = U_pre
            flag_used[d_pre] = 1
    
    if test == 1:
        print('(', final_type, ')')
    
    for i in range(0, dim+1):
        if final_type[i] == '?' and final_type[dim - i] != '?':
            i1 = dim - i
            final_type[i] = final_type[i1] - i1 + dim/2
    
    final_type[0] = 0
    
    for i in range(1, dim+1):
        if final_type[i] == '?':
            prev = final_type[i-1]
            if prev != '?' and prev in final_type[i+1:]:
                final_type[i] = prev
                
    for i in range(1, dim+1):
        if final_type[i] == '?':
            final_type[i] = min(final_type[i-1] + 1, dim/2)
    
    if is_final(final_type, dim/2):
        return final_type[1:dim/2 + 1]
    print('error:', final_type[1:dim/2 + 1])
    
def is_final(final_type, dim):
    n = len(final_type)
    if final_type[0] != 0:
        return 0
    
    if final_type[n-1] != dim:
        return 0
    
    for i in range(1, n):
        if final_type[i] != final_type[i - 1] and final_type[i] != final_type[i - 1] + 1:
            return 0
    return 1

In [24]:
def dzialanie(f, m, p):
    Rx.<x> = PolynomialRing(GF(p))
    fp = Rx(f(x^p))
    C = superelliptic(fp, m, p)
    holo = C.basis_holomorphic_differentials
    
    Rxy.<x, y> = PolynomialRing(GF(p), 2)
    kxi1.<xi1> = PolynomialRing(FractionField(Rxy))
    kxi = kxi1.quotient(xi1^p)
    xi = kxi(xi1)
    holo_forms = [a.form for a in holo]
    holo_xi = [kxi(a(x = x+xi, y = y)) for a in holo_forms]
    
    N = matrix(kxi1, C.genus(), C.genus())
    for i in range(0, p):
        M = matrix(GF(p), C.genus(), C.genus())
        for j in range(0, len(holo_xi)):
            a = holo_xi[j]
            omega = superelliptic_form(C, a[i])
            v = omega.coordinates()
            M[j, :] = v
        N += xi1^i*M
    return N

def bloki(A):
    B = A.jordan_form(subdivide=True)
    lista = []
    d = 0
    i = 0
    while d < B.dimensions()[1]:
        lista.append(B.subdivision(i, i).dimensions()[1])
        d = d + B.subdivision(i, i).dimensions()[1]
        i = i+1
    return lista

def p_cov(C):
    m = C.exponent
    p = C.characteristic
    f = C.polynomial
    return superelliptic(f(x^p), m, p)

# Testy

In [33]:
p = 5
Rx.<x> = PolynomialRing(GF(p))
r = 3
f = x^(r) + x + 1
m = 12
A = dzialanie(f, m, p)
print(bloki(A))
C = superelliptic(f, m, p)
print(C.genus(), p_cov(C).genus())

[5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 4, 4, 3, 3, 3, 2, 2, 2, 1, 1, 1]


10 76


In [79]:
omega = C.basis_holomorphic_differentials[2]

In [81]:
lista = [a.form for a in C.basis_holomorphic_differentials]

In [82]:
kxi1.<xi1> = PolynomialRing(FractionField(Rxy))
kxi = kxi1.quotient(xi1^p)
xi = kxi(xi1)

In [96]:
lista2 = [kxi(a(x = x+xi, y = y)) for a in lista]

In [92]:
kxi(x)

x

In [98]:
a = lista2[0]

In [99]:
omega.form(x = x+xi, y = y)

1/y*xi1bar^2 + 2*x/y*xi1bar + x^2/y

In [15]:
omega1 = superelliptic_form(C, omega.form(x = x+xi, y = y))

TypeError: cannot convert 1/y*xi1bar^2 + 2*x/y*xi1bar + x^2/y/1 to an element of Fraction Field of Multivariate Polynomial Ring in x, y over Finite Field of size 5

In [68]:
kxi1.<xi> = PolynomialRing(GF(p))
kxi = FractionField(kxi1)
Rxy.<x, y> = PolynomialRing(kxi, 2)
Fxy = FractionField(Rxy)

Rx.<x> = PolynomialRing(kxi)
Fx = FractionField(Rx)
FxRy.<y> = PolynomialRing(Fx)

In [69]:
C.basis_holomorphic_differentials

x/y

In [5]:
p = 5
Rx.<x> = PolynomialRing(GF(p))
f = Rx(x^7 + x + 1)
m = 2
Rxy.<x, y> = PolynomialRing(GF(p), 2)
print(dzialanie(f, m, p))
A = dzialanie(f, m, p)

[       1        0        0        0        0        0        0        0        0        0        0        0        0        0        0        0        0]
[     xi1        1        0        0        0        0        0        0        0        0        0        0        0        0        0        0        0]
[   xi1^2    2*xi1        1        0        0        0        0        0        0        0        0        0        0        0        0        0        0]
[   xi1^3 -2*xi1^2   -2*xi1        1        0        0        0        0        0        0        0        0        0        0        0        0        0]
[   xi1^4   -xi1^3    xi1^2     -xi1        1        0        0        0        0        0        0        0        0        0        0        0        0]
[       0        0        0        0        0        1        0        0        0        0        0        0        0        0        0        0        0]
[       0        0        0        0        0      xi1        1       

In [11]:
A.jordan_form()

[1 1 0 0 0|0 0 0 0 0|0 0 0 0 0|0 0]
[0 1 1 0 0|0 0 0 0 0|0 0 0 0 0|0 0]
[0 0 1 1 0|0 0 0 0 0|0 0 0 0 0|0 0]
[0 0 0 1 1|0 0 0 0 0|0 0 0 0 0|0 0]
[0 0 0 0 1|0 0 0 0 0|0 0 0 0 0|0 0]
[---------+---------+---------+---]
[0 0 0 0 0|1 1 0 0 0|0 0 0 0 0|0 0]
[0 0 0 0 0|0 1 1 0 0|0 0 0 0 0|0 0]
[0 0 0 0 0|0 0 1 1 0|0 0 0 0 0|0 0]
[0 0 0 0 0|0 0 0 1 1|0 0 0 0 0|0 0]
[0 0 0 0 0|0 0 0 0 1|0 0 0 0 0|0 0]
[---------+---------+---------+---]
[0 0 0 0 0|0 0 0 0 0|1 1 0 0 0|0 0]
[0 0 0 0 0|0 0 0 0 0|0 1 1 0 0|0 0]
[0 0 0 0 0|0 0 0 0 0|0 0 1 1 0|0 0]
[0 0 0 0 0|0 0 0 0 0|0 0 0 1 1|0 0]
[0 0 0 0 0|0 0 0 0 0|0 0 0 0 1|0 0]
[---------+---------+---------+---]
[0 0 0 0 0|0 0 0 0 0|0 0 0 0 0|1 1]
[0 0 0 0 0|0 0 0 0 0|0 0 0 0 0|0 1]

In [19]:
M = matrix(Rx, 3,3)

In [24]:
M = matrix(Rx, [[x, 1, 1], [1,2,3], [x+1,2,4]])

In [25]:
M.rank()

3

In [28]:
kxi1.<xi1> = PolynomialRing(FractionField(Rxy))
kxi = kxi1.quotient(xi1^p)
xi = kxi(xi1)

In [33]:
lift(xi^5)

0

In [35]:
E = EllipticCurve(GF(3), [1,1])

In [2]:
p = 5
R.<x> = PolynomialRing(GF(p))
f = x^3 + x + 1
m = 2
C = superelliptic(f, m, p)
C.verschiebung_matrix()

[2 0]
[2 0]